https://drive.google.com/drive/u/0/folders/1q4iseizCdmC5Wx9G4KeNvcsH8SZrKF4b


<center> <b>Machine Learning - SBU FALL 2024</b></center>

In [ ]:
Student_Number = '99243022'
Name = 'Masoume'
Last_Name = 'Pasebani'

In this notebook, you are expected to implement a fully functional MLP (Multi-Layer Perceptron) neural network from scratch.
You are not allowed to use any libraries (including numpy). You will use the **Iris dataset** for training and testing your network, focusing on reducing the error on this dataset.


**modify iris dataset to a version compatible with this task : binary classifiaction of if a flower is setosa (1) or not(-1)**

# Automatic Differentiation

Automatic differentiation has two main methods: forward mode and reverse mode.
PyTorch uses the reverse mode approach, and we will also use this method in this project.

To learn this concept, simply click on this [link](https://auto-ed.readthedocs.io/en/latest/mod3.html#i-the-basics-of-reverse-mode)
and read only the section "Intuition for Example An IV" up to the end of step six.

Essentially, you need to consider a data structure to build a computational graph.
By calling the `backward` function on the network's output, you can compute the derivative of the output
with respect to all weights and biases of the network. (In this case, our network has only one output.)


## Visualization Tool

In [ ]:
from graphviz import Digraph


def trace(root):
    nodes, edges = set(), set()

    def build(v):
        if v not in nodes:
            nodes.add(v)
            for child in v.children:
                edges.add((child, v))
                build(child)

    build(root)
    return nodes, edges


def draw_dot(root, format='svg', rankdir='LR'):
    """
    format: png | svg | ...
    rankdir: TB (top to bottom graph) | LR (left to right)
    """
    assert rankdir in ['LR', 'TB']
    nodes, edges = trace(root)
    dot = Digraph(format=format, graph_attr={'rankdir': rankdir})  # , node_attr={'rankdir': 'TB'})

    for n in nodes:
        dot.node(name=str(id(n)), label="{ %s | data %.4f | grad %.4f }" % (n.label, n.value, n.grad), shape='record')
        if n.operator:
            dot.node(name=str(id(n)) + n.operator, label=n.operator)
            dot.edge(str(id(n)) + n.operator, str(id(n)))

    for n1, n2 in edges:
        dot.edge(str(id(n1)), str(id(n2)) + n2.operator)

    return dot

# **Tensor**
This class serves as a data structure for storing values and supporting operations such as addition, multiplication, and division. It also implements automatic differentiation.

---
sub method: in this method Instead of defining a separate subtraction logic, it reuses addition (+) by adding the negative of other.


 mul method: This method multiplies two tensors element-wise and tracks the operation for gradient computation.
Combines the values.
Builds the computational graph by storing the relationship in children.
Defines a backward function to compute gradients during backpropagation.
For z = x * y, the gradients are:
∂𝑧/∂𝑥=𝑦
∂𝑧/∂𝑦=𝑥


rmul method: Enables scalar multiplication where the scalar is on the left-hand side, such as 2⋅Tensor(x).


pow method: This method Raises the tensor value to a power.
Computes 𝑥^𝑛 and stores the relationship.
Defines a backward function to compute gradients using:
∂𝑧/∂𝑥=𝑛⋅𝑥^(𝑛−1)


truediv method: this method performs element-wise division if the second operand is a tensor.
Handles scalar division when the second operand is a scalar.
Tracks the operation for gradient computation and creates a backward function.
Gradient Logic:
For z=x/y:
∂z/∂x=1/y
∂z/∂y=- x/y^2

backward method: This method propagates gradients backwards through the computational graph, enabling automatic differentiation.
Computes the gradients of all tensors involved in the computation, starting from the final result.
backward processes the computational graph in reverse topological order.
For each tensor, it calls the _backward method to update its parents' gradients.



In [ ]:
class Tensor:

  def __init__(self, value, label='', children=(), operator=None):
    self.value = value
    self.children = set(children)
    self.operator = operator
    self.grad = 0
    self._backward = lambda  : None
    self.label = label


  def __repr__(self) -> str:
    return f"Tensor(label = {self.label}, value = {self.value}, grad = {self.grad}, operator = {self.operator})"

  # normal add
  def __add__(self, other):

    other = other if isinstance(other, Tensor) else Tensor(other)

    out_value = self.value + other.value
    out = Tensor(out_value, children=(self, other), operator='+')

    def backward():
      self.grad = 1 * out.grad
      other.grad = 1 * out.grad

    out._backward = backward

    return out

  # reverse add
  def __radd__(self, other):
    return self + other

  def __sub__(self, other):
    # TODO
    return self + (-other)


  def __mul__(self, other):
    # TODO
    other = other if isinstance(other, Tensor) else Tensor(other)
    out = Tensor(self.value * other.value, children=(self, other), operator='*')

    def backward():
      self.grad += other.value * out.grad
      other.grad += self.value * out.grad

    out._backward = backward
    return out

  def __rmul__(self, other):
    # TODO
    return self * other

  def __truediv__(self, other):
    # TODO
    other = other if isinstance(other, Tensor) else Tensor(other)
    return self * (other ** -1)


  def __pow__(self, other):
    # TODO
    input_value = self.value
    output_value = math.pow(input_value, other)

    out = Tensor(output_value, children=(self,), operator='pow')

    def backward():
      self.grad += other * math.pow(self.value, other - 1) * out.grad

    out._backward = backward
    return out


  def backward(self):
    # TODO
    topo_sort = []
    visited_set = set()

    def build_topo(v):
      for child in v.children:
        if child not in visited_set:
          visited_set.add(v)
          build_topo(child)

      topo_sort.append(v)
    build_topo(self)

    for i in reversed(topo_sort):
      i._backward()


# Activation Functions

the tanh function performs the hyperbolic tangent operation on a custom Tensor object, integrating both forward computation and automatic differentiation. It ensures the input is a Tensor (or wraps it if not), computes the tanh value using math.tanh, and stores the result in a new Tensor while tracking the input tensor (x) as a dependency in the computational graph. The derivative of tanh, 1−tanh^2(x), is used in the nested backward function to compute and propagate gradients during backpropagation. This function is assigned to the output tensor’s _backward attribute, enabling gradient computation when the backward method is called. Finally, the function returns the output tensor, fully equipped with its value and gradient propagation logic.

In [ ]:
class F:

  @staticmethod
  def tanh(x: Tensor) -> Tensor:
    # TODO
    x = x if isinstance(x, Tensor) else Tensor(x)

    out=Tensor(math.tanh(x.value),children=(x, ), operator='tanh')
    def backward():
      x.grad += (1 - out.value ** 2) * out.grad

    out._backward = backward

    return out

# Neuron, Layer & MLP (Forward Section)

forward: This method computes the neuron's output by multiplying inputs with weights and passing the result through the tanh activation function.

Purpose: Returns all trainable parameters (weights and bias).

In [ ]:
class Neuron:

  def __init__(self, input_size):

    self.weights = [Tensor(random.uniform(-1, 1)) for i in range(input_size)]
    self.bias = Tensor(random.uniform(-1, 1))

  def forward(self, x):
    # TODO
    activation = [w_i * x_i for w_i, x_i in zip(self.weights, x)]
    tens = Tensor(0)
    for r in activation:
      tens += r

    return F.tanh(tens + self.bias)

  def __call__(self, x):
    # TODO
    return self.forward(x)


  def parameters(self):
    # TODO
    return self.weights + [self.bias]

  def __print__(self):
    # TODO
    print(f"weights : {self.weights}")
    print(f"bias : {self.bias}")


forward: this method passes the input through all neurons in the layer.
Each neuron's forward method is called.The outputs are collected into a list.

parameters: this method collects and returns the parameters of all neurons in the layer.

In [ ]:
class Layer:

  def __init__(self, input_size, output_size):
    self.neurons = [Neuron(input_size) for _ in range(output_size)]

  def forward(self, x):
    # TODO
    res = [neuron(x) for neuron in self.neurons]
    return res[0] if len(res)==1 else res


  def __call__(self, x):
    # TODO
    return self.forward(x)

  def parameters(self):
    # TODO
    p = []
    for neuron in self.neurons:
      for pr in neuron.parameters():
        p.append(pr)
    return p

  def __print__(self):
    # TODO
    for neuron in self.neurons:
      neuron.__print__()

# The MLP Class Structure

The `MLP` class is expected to have three main methods, which you should implement with the same structure:

1. **`forward` Method:**  
   This method performs calculations on the input and returns the output.

2. **`__call__` Method:**  
   This method simply calls the `forward` method. Essentially, we want to pass the input to the model in this way: `model(x)`.

3. **`parameters` Method:**  
   This method returns all the weights of the network in a list.

---

# Layers in the MLP

The `MLP` class itself consists of several layers (referred to as `Layer`), which are the actual layers of the neural network. Each layer needs to know:
- The dimensions of the input data.
- The dimensions of the output data.

In this project, all inputs are vectors. Each `Layer` consists of several neurons. For example:
- If a layer receives a 7-dimensional vector as input (input size) and produces a 4-dimensional vector as output, then:
  - The layer should have 4 neurons.
  - Each neuron should have 7 weights and 1 bias.

You should implement the details and structure of the layers and neurons according to the given explanation.


forward: This method sequentially processes the input x through each layer of the network, with the output of one layer becoming the input to the next.

parameters:
This method collects the parameters of all layers in the network and returns them as a single list.

In [ ]:
class MLP:

  def __init__(self, input_size, layer_sizes):
    layers_total = [input_size] + layer_sizes
    self.layers = [Layer(layers_total[i], layers_total[i+1]) for i in range(len(layer_sizes))]

  def forward(self, x):
    # TODO
    for layer in self.layers:
      x = layer(x)
    return x

  def __call__(self, x):
    # TODO
    return self.forward(x)

  def parameters(self):
    # TODO
    p = []
    for layer in self.layers:
      for pr in layer.parameters():
        p.append(pr)

      return p

  def __print__(self):
    # TODO
    for layer in self.layers:
      layer.__print__()

# Optimizer

Similar to the first project, the `optimizer` should have access to the network's weights.
This time, it must update them based on their derivatives and the value of the `lr` parameter (learning rate).

- **`step` Method:**  
  This method functions similarly to the `update` method in the previous project. It updates the weights of the network.

- **`grad_zero` Method:**  
  An additional method called `grad_zero` is included, whose functionality has been explained. It is used to reset the gradients of the weights to zero after each update step.


zero_grad:This method resets all gradients of the parameters to zero to prevent gradient accumulation between iterations

step: This method updates the parameters using the computed gradients and learning rate with the formula w = w - lr * grad.

In [ ]:
class Optimizer:
  def __init__(self, parameters, lr=0.01):
    self.parameters = parameters
    self.lr = lr

  def zero_grad(self):
    # TODO
    for p in self.parameters:
      p.grad = 0

  def step(self):
    # TODO
    for p in self.parameters:
      p.value -= self.lr * p.grad

# Training Part

Prepeare the dataset in this section in bellow code snippet we place a toy example dataset just for better clarification

In [ ]:
X = [
    [2.0, 3.0, -1.0],
    [3.0, -1.0, 0.5],
    [0.5, 1.0, 1.0],
    [1.0, 1.0, -1.0]
]

Y = [1.0, -1.0, -1.0, 1.0]

this code defines a data sampling function for creating a controlled subset from a dataset, with specific emphasis on balancing samples between a target class and other classes. It uses the Iris dataset, which is scaled using StandardScaler for normalization. The sample_classes function takes the feature matrix X, labels Y, a target class, the number of samples to draw from the target class (n_target), and a range (min_other, max_other) for the number of samples to randomly select from other classes. The function identifies indices corresponding to the target class and other classes, randomly samples the specified number of data points without replacement, and returns the selected samples and labels.

The parameters are set to sample 30 data points from the target class (class 0), while 2 to 15 samples are randomly chosen for each of the other classes. The sampling ensures diversity in the dataset by combining a fixed number of samples from the target class with variable numbers from the other classes. This approach is useful for creating balanced or tailored datasets for training or testing machine learning models.

In [ ]:
# TODO
import numpy as np
from sklearn.datasets import load_iris
from sklearn.preprocessing import StandardScaler
import random
import math


iris = load_iris()
X = iris.data
Y = iris.target

scaler = StandardScaler()
X = scaler.fit_transform(X)

# Function to sample data
def sample_classes(X: np.ndarray, Y: np.ndarray, target_class: int, n_target: int, min_other: int, max_other: int):
    sampled_X = []
    sampled_Y = []

    # Sample `n_target` from the target class
    target_indices = np.where(Y == target_class)[0]
    sampled_target_indices = np.random.choice(target_indices, n_target, replace=False)
    sampled_X.extend(X[sampled_target_indices])
    sampled_Y.extend(Y[sampled_target_indices])

    other_classes = [cls for cls in np.unique(Y) if cls != target_class]
    for cls in other_classes:
        other_indices = np.where(Y == cls)[0]
        n_other = np.random.randint(min_other, max_other + 1)
        sampled_other_indices = np.random.choice(other_indices, n_other, replace=False)
        sampled_X.extend(X[sampled_other_indices])
        sampled_Y.extend(Y[sampled_other_indices])

    return np.array(sampled_X), np.array(sampled_Y)

# Parameters
n_target = 30
min_other = 2
max_other = 15

target_class = 0

# Sample the data
sampled_X, sampled_Y = sample_classes(X, Y, target_class, n_target, min_other, max_other)




## Loss Function (SE)

In [ ]:
from typing import List

def criterion(y_hats: List[Tensor], Y) -> Tensor:
  return sum([(y_hat - y)**2 for y_hat, y in zip(y_hats, Y)])

# Training Steps for the Model

1. **Calculate Model Predictions:**  
   For each input `x`, compute the output of the model, `y_hat`.

2. **Compute Error:**  
   Calculate the error of the predictions using the Mean Squared Error (MSE) loss function for simplicity.

3. **Reset Gradients of Network Variables:**  
   Set the gradients of all variables in the network to zero. Once you implement automatic differentiation, you will understand why this step is necessary.

4. **Compute Derivatives:**  
   This is the most challenging part of the project. When this function is called, you need to calculate the derivative of the `loss` with respect to all weights and biases of the network.  
   To implement this, you will use **Automatic Differentiation (AutoDiff)**.

5. **Update Network Weights:**  
   The `optimizer` will use the derivatives of the `loss` with respect to all weights and biases to update them in a direction that reduces the error in the next step.


This method calculates the total loss for all samples. It also initializes the gradient for backpropagation.

In [ ]:
def compute_loss(y_hats, real_y):
    total_loss = Tensor(0)
    for y_hat, y in zip(y_hats, real_y):
        loss = (y_hat - y) ** 2
        total_loss += loss
    # backward propagation to compute gradients based on loss gradient
    total_loss.grad = 1

    return total_loss

In [ ]:
n_epochs = 20

input_size = 3 # Number of features in the input layer
layer_sizes = [2, 3, 1] # Number of neurons in each hidden and output layer
model = MLP(input_size, layer_sizes)
optim = Optimizer(model.parameters(), lr=0.01)
for i in range(n_epochs):
  # Forward pass: Compute predictions for the entire dataset
  y_hats = [model(_X) for _X in sampled_X]

  loss = criterion(y_hats, sampled_Y)
  # Compute the loss
  loss = compute_loss(y_hats, sampled_Y)

  # Zero the gradients to prevent accumulation from previous iterations
  optim.zero_grad()

  # Backward pass: Compute the gradient of the loss function with respect to model parameters
  loss.backward()

  # Update the model parameters using the optimizer
  optim.step()

draw_dot(loss)

In [ ]:
for y_pred in y_hats:
    print(y_pred.value)

-0.3272053312743154
-0.3026325618635415
-0.3420494221229964
-0.21245171608529811
-0.4042310539934074
-0.31184691270541826
-0.39846690773415905
-0.23154956075326494
-0.31436650709887826
-0.5631101517354627
-0.28344785815221113
-0.6223836840490051
-0.3394992197563923
-0.3242811719649928
-0.24025085147919373
-0.2328913935261273
-0.22584596691281983
-0.2318990567753011
-0.3018554676179971
-0.33286163069675173
-0.3242811719649928
-0.29293739074486147
-0.32120779726857246
-0.29775289905529106
-0.27877669408551375
-0.3028748202497163
-0.315898300870196
-0.4383817356500441
-0.21368588628013585
-0.46455643488565385
0.3858964391314457
0.301375764438408
0.23328091905850262
0.29849075355099425
0.2890698602530442
0.3675379451091566
0.26405872576054906
0.3719677257423346
0.4009850085971914
0.35640998464155976
0.3866370611998037
0.22400886182911575
0.39749400280287034
0.4316519874887227
0.1825912470846227
0.32788493306557565
0.19320076609275974
0.36215713901832514
0.24272905646335938
0.30426497703551